<a href="https://colab.research.google.com/github/alu0101132945/TFG/blob/main/collabBERTTOPIC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install bertopic

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 3.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 23.5 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 85.7/85.7 kB 10.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 171.5/171.5 kB 17.7 MB/s eta 0:00:00
  Using cached Cython-0.29.37-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.manylinux_2_24_x86_64.whl (1.9 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 kB 7.3 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (7

Importamos las librerias necesarias para poder trabajar con el modelo

In [ ]:
import requests
import json
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import nltk
from bertopic import BERTopic
from sklearn.feature_extraction.text import CountVectorizer

from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.probability import FreqDist

import string

import re

In [ ]:
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
lemmatizer = WordNetLemmatizer()

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


In [ ]:
def tokenize_lowercase(text):
  stop_words = stopwords.words('spanish')

  #add punctuation char's to stopwords list
  stop_words += list(string.punctuation) # <-- contains !"#$%&'()*+,-./:;<=>?@[\]^_`{|}~

  #añadimos los numeros y otras palabras sin valor
  stop_words += ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9']
  stop_words += ['xi','sra','sr.','consejero','consejera','legislatura','dirigida', 'presidente','vicepresidente']
  tokens = word_tokenize(text)
  stopwords_removed = [token.lower() for token in tokens if token.lower() not in stop_words]

  return stopwords_removed

In [ ]:
def remove_nums(text_object):
  no_nums = list(filter(lambda x: x.isalpha(), text_object))
  return no_nums

In [ ]:
def lemmatize_text(df_text):
    lemmatized =[]
    processed = []
    for w in df_text:
        lemmatized.append(lemmatizer.lemmatize(w))
        processed = list(filter(lambda x: x.isalpha(), lemmatized))
    return processed

In [ ]:
# guardamos la URL con la info de los grupos
url = "https://parcan.es/api/informacion_grupos/11/"

# Hacemos una petición GET a la API
grupos_resp = requests.get(url)

# Intentar cargar el contenido como JSON
try:
    grupos_json = grupos_resp.json()
    grupos = grupos_json.get('result')

    # Si la carga es exitosa, procede con la extracción de los valores
    id_organo_ids = []

    # Itera sobre cada diccionario en la lista result
    for grupo in grupos:
      id_organo_id = grupo['id_organo_id']
      id_organo_ids.append(id_organo_id)

except json.JSONDecodeError:
    # Si no se puede cargar como JSON, probablemente sea una cadena
    print("El contenido de la respuesta no es un objeto JSON válido.")

In [ ]:
base_url = "https://parcan.es/api/informacion_grupos/iniciativas/{}"
urls = [base_url.format(code) for code in id_organo_ids]

In [ ]:
extractos = []
for ini_url in urls:
  iniciativas_resp = requests.get(ini_url)
  try:
    iniciativas_json = iniciativas_resp.json()
    iniciativas = iniciativas_json.get('result')
    for iniciativa in iniciativas:
      extracto = iniciativa['extracto']
      extractos.append(extracto)
  except json.JSONDecodeError:
    print("El contenido de la respuesta no es un objeto JSON válido.")
print(extractos)

['el reto demográfico y el equilibrio poblacional en Canarias.', 'la revisión del Régimen Económico y Fiscal de Canarias.', 'Consejo Canario de la Cultura.', 'Grupo Parlamentario Socialista Canario.', 'De la Sra. consejera de Sanidad, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Transición Ecológica y Energía, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Turismo y Empleo, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Universidades, Ciencia e Innovación y Cultura, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Agricultura, Ganadería, Pesca y Soberanía Alimentaria, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Hacienda y Relaciones con la Unión Europea, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Bienestar Social,

In [ ]:
extracto_token = []
for extracto in extractos:
  extracto_token.append(tokenize_lowercase(extracto))

for extracto in extracto_token:
  extracto = remove_nums(extracto)

for extracto in extracto_token:
 extracto = lemmatize_text(extracto)

for i in range(len(extracto_token)):
  extracto_token[i] = " ".join(extracto_token[i])
print(extracto_token)

['reto demográfico equilibrio poblacional canarias', 'revisión régimen económico fiscal canarias', 'consejo canario cultura', 'grupo parlamentario socialista canario', 'sanidad líneas estratégicas desarrollar', 'transición ecológica energía líneas estratégicas desarrollar', 'turismo empleo líneas estratégicas desarrollar', 'universidades ciencia innovación cultura líneas estratégicas desarrollar', 'agricultura ganadería pesca soberanía alimentaria líneas estratégicas desarrollar', 'hacienda relaciones unión europea líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'economía industria comercio autónomos líneas estratégicas desarrollar', 'educación formación profesional actividad física deportes líneas estratégicas desarrollar', 'presidencia administraciones públicas justicia seguridad líneas estratégicas desarrollar', 'hacienda r

In [ ]:
topic_model = BERTopic(language="spanish",calculate_probabilities=True, verbose=True)

In [ ]:
topics, probs = topic_model.fit_transform(extracto_token)
hierarchical_topics = topic_model.hierarchical_topics(extracto_token)

2024-05-22 16:54:07,177 - BERTopic - Embedding - Transforming documents to embeddings.


modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/4.12k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/9.08M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

Batches:   0%|          | 0/186 [00:00<?, ?it/s]

2024-05-22 16:57:15,238 - BERTopic - Embedding - Completed ✓
2024-05-22 16:57:15,240 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 16:57:59,873 - BERTopic - Dimensionality - Completed ✓
2024-05-22 16:57:59,875 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 16:58:02,715 - BERTopic - Cluster - Completed ✓
2024-05-22 16:58:02,736 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 16:58:02,999 - BERTopic - Representation - Completed ✓
100%|██████████| 103/103 [00:00<00:00, 191.04it/s]


In [ ]:
topic_model.get_topics()

{-1: [('profesional', 0.011009066800547423),
  ('deportes', 0.010720343141223358),
  ('formación', 0.010610484575473504),
  ('educación', 0.010512227732090563),
  ('actividad', 0.010421305984621805),
  ('física', 0.010397173839026887),
  ('vivienda', 0.00940219713502771),
  ('públicas', 0.009139419455025293),
  ('obras', 0.008779748973909486),
  ('movilidad', 0.008349163622141519)],
 0: [('turismo', 0.08232995419152239),
  ('empleo', 0.07592411022478479),
  ('turístico', 0.02770086954190382),
  ('turística', 0.026819947306749334),
  ('laboral', 0.01592661023524769),
  ('turísticas', 0.01484906810584768),
  ('medidas', 0.014025563051713782),
  ('vacacionales', 0.012282167656158907),
  ('temporada', 0.010298430744160916),
  ('islas', 0.010165160188697056)],
 1: [('universidades', 0.10515728502628639),
  ('innovación', 0.1013448315329499),
  ('ciencia', 0.10104345725582399),
  ('cultura', 0.1001267560401651),
  ('cultural', 0.02020742889822463),
  ('investigación', 0.013077614913912237),


In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=97)

In [ ]:
topic_model.visualize_heatmap(n_clusters=20,width=1000,height=1000)

In [ ]:
topic_model.reduce_topics(extracto_token, nr_topics=30)

2024-05-22 16:58:12,443 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 16:58:12,682 - BERTopic - Topic reduction - Reduced number of topics from 105 to 30


In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=40)

In [ ]:
topic_model.visualize_barchart(top_n_topics=8)

In [ ]:
extractos = {
    'extractos1': [],
    'extractos2': [],
    'extractos3': [],
    'extractos4': [],
    'extractos5': [],
    'extractos6': [],
    'extractos7': []
}
for i, ini_url in enumerate(urls):
    iniciativas_resp = requests.get(ini_url)
    try:
        iniciativas_json = iniciativas_resp.json()
        iniciativas = iniciativas_json.get('result')

        # Obtener el nombre de la variable de extractos
        nombre_variable = f'extractos{i+1}'

        # Obtener la lista de extractos correspondiente
        lista_extractos = extractos[nombre_variable]

        # Agregar extractos a la lista correspondiente
        for iniciativa in iniciativas:
            extracto = iniciativa['extracto']
            lista_extractos.append(extracto)

    except json.JSONDecodeError:
        print("El contenido de la respuesta no es un objeto JSON válido.")
for lista_extractos in extractos.values():
    # Extender la lista de todos_los_extractos con los extractos de la lista actual
    print(lista_extractos)

['el reto demográfico y el equilibrio poblacional en Canarias.', 'la revisión del Régimen Económico y Fiscal de Canarias.', 'Consejo Canario de la Cultura.', 'Grupo Parlamentario Socialista Canario.', 'De la Sra. consejera de Sanidad, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Transición Ecológica y Energía, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Turismo y Empleo, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Universidades, Ciencia e Innovación y Cultura, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'Del Sr. consejero de Agricultura, Ganadería, Pesca y Soberanía Alimentaria, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Hacienda y Relaciones con la Unión Europea, sobre las líneas estratégicas a desarrollar en la XI Legislatura.', 'De la Sra. consejera de Bienestar Social,

In [ ]:
extractos_token = {
    'extractos_token1': [],
    'extractos_token2': [],
    'extractos_token3': [],
    'extractos_token4': [],
    'extractos_token5': [],
    'extractos_token6': [],
    'extractos_token7': []
}
for i, extractos_text in enumerate(extractos.values()):
    for extrac in extractos_text:
      # Tokenizar el extracto, eliminar números y lematizar
        extrac_processed = tokenize_lowercase(extrac)
        extrac_processed = remove_nums(extrac_processed)
        extrac_processed = lemmatize_text(extrac_processed)

        # Unir los tokens en una sola cadena
        extrac_processed_str = ' '.join(extrac_processed)

        # Agregar la cadena procesada a la lista correspondiente en extractos_token
        extractos_token[f'extractos_token{i+1}'].append(extrac_processed_str)


for lista_extractos in extractos_token.values():
  # Extender la lista de todos_los_extractos con los extractos de la lista actual
  print(lista_extractos)

['reto demográfico equilibrio poblacional canarias', 'revisión régimen económico fiscal canarias', 'consejo canario cultura', 'grupo parlamentario socialista canario', 'sanidad líneas estratégicas desarrollar', 'transición ecológica energía líneas estratégicas desarrollar', 'turismo empleo líneas estratégicas desarrollar', 'universidades ciencia innovación cultura líneas estratégicas desarrollar', 'agricultura ganadería pesca soberanía alimentaria líneas estratégicas desarrollar', 'hacienda relaciones unión europea líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'bienestar social igualdad juventud infancia familias líneas estratégicas desarrollar', 'economía industria comercio autónomos líneas estratégicas desarrollar', 'educación formación profesional actividad física deportes líneas estratégicas desarrollar', 'presidencia administraciones públicas justicia seguridad líneas estratégicas desarrollar', 'hacienda r

modelo del primer grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token1'))

2024-05-22 16:58:27,124 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/61 [00:00<?, ?it/s]

2024-05-22 16:59:19,999 - BERTopic - Embedding - Completed ✓
2024-05-22 16:59:20,001 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 16:59:32,584 - BERTopic - Dimensionality - Completed ✓
2024-05-22 16:59:32,587 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 16:59:32,851 - BERTopic - Cluster - Completed ✓
2024-05-22 16:59:32,854 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 16:59:32,944 - BERTopic - Representation - Completed ✓
2024-05-22 16:59:32,947 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 16:59:33,035 - BERTopic - Topic reduction - Reduced number of topics from 34 to 30


In [ ]:
topic_model.get_topic(0)

[('juventud', 0.11856873472748113),
 ('infancia', 0.11680851062491004),
 ('familias', 0.11370615084025561),
 ('igualdad', 0.113447114635704),
 ('bienestar', 0.11031193738233754),
 ('social', 0.10968009069172759),
 ('persona', 0.03603467392940419),
 ('plaza', 0.03259342189934001),
 ('discapacidad', 0.032041179630574505),
 ('dependencia', 0.028337528580900096)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=20,width=1000,height=1000)

modelo del segundo grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token2'))

2024-05-22 16:59:34,808 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/34 [00:00<?, ?it/s]

2024-05-22 17:00:03,981 - BERTopic - Embedding - Completed ✓
2024-05-22 17:00:03,989 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 17:00:11,037 - BERTopic - Dimensionality - Completed ✓
2024-05-22 17:00:11,040 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 17:00:11,149 - BERTopic - Cluster - Completed ✓
2024-05-22 17:00:11,152 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 17:00:11,208 - BERTopic - Representation - Completed ✓
2024-05-22 17:00:11,212 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 17:00:11,218 - BERTopic - Topic reduction - Reduced number of topics from 18 to 18


In [ ]:
topic_model.get_topic(0)

[('educación', 0.13358361692633186),
 ('profesional', 0.1270400895055298),
 ('deportes', 0.12472439776321516),
 ('formación', 0.12453576679545673),
 ('física', 0.12368974083636192),
 ('actividad', 0.11573940215194738),
 ('centros', 0.03944297908260072),
 ('escuelas', 0.03182733679232989),
 ('educativos', 0.03136280486435641),
 ('escolar', 0.02582819224123469)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=15,width=1000,height=1000)

modelo del tercer grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token3'))

2024-05-22 17:00:12,794 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/33 [00:00<?, ?it/s]

2024-05-22 17:00:38,420 - BERTopic - Embedding - Completed ✓
2024-05-22 17:00:38,423 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 17:00:43,942 - BERTopic - Dimensionality - Completed ✓
2024-05-22 17:00:43,944 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 17:00:44,049 - BERTopic - Cluster - Completed ✓
2024-05-22 17:00:44,053 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 17:00:44,111 - BERTopic - Representation - Completed ✓
2024-05-22 17:00:44,114 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 17:00:44,119 - BERTopic - Topic reduction - Reduced number of topics from 21 to 21


In [ ]:
topic_model.get_topic(0)

[('alimentaria', 0.1792434564577934),
 ('ganadería', 0.17351331663934944),
 ('agricultura', 0.17351331663934944),
 ('pesca', 0.172050382953376),
 ('soberanía', 0.1715693554182834),
 ('sector', 0.051438066133163374),
 ('primario', 0.03800728593596028),
 ('producción', 0.023117666627104582),
 ('cultivo', 0.022055829876481508),
 ('tropical', 0.022055829876481508)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=13,width=1000,height=1000)

modelo del cuarto grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token4'))

2024-05-22 17:00:45,717 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/12 [00:00<?, ?it/s]

2024-05-22 17:00:56,999 - BERTopic - Embedding - Completed ✓
2024-05-22 17:00:57,002 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 17:01:00,103 - BERTopic - Dimensionality - Completed ✓
2024-05-22 17:01:00,105 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 17:01:00,138 - BERTopic - Cluster - Completed ✓
2024-05-22 17:01:00,140 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 17:01:00,174 - BERTopic - Representation - Completed ✓
2024-05-22 17:01:00,176 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 17:01:00,180 - BERTopic - Topic reduction - Reduced number of topics from 14 to 14


In [ ]:
topic_model.get_topic(0)

[('educación', 0.13906120257407467),
 ('deportes', 0.13681967227692832),
 ('actividad', 0.13681967227692832),
 ('formación', 0.13566392089194512),
 ('profesional', 0.13505166332264354),
 ('física', 0.13325543743234958),
 ('centros', 0.04502470467133105),
 ('educativos', 0.04065856362967606),
 ('plan', 0.039630037165748234),
 ('educativas', 0.03376746007503978)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=7,width=1000,height=1000)

modelo del quinto grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token5'))

2024-05-22 17:01:01,615 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/19 [00:00<?, ?it/s]

2024-05-22 17:01:18,533 - BERTopic - Embedding - Completed ✓
2024-05-22 17:01:18,539 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 17:01:24,904 - BERTopic - Dimensionality - Completed ✓
2024-05-22 17:01:24,907 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 17:01:24,963 - BERTopic - Cluster - Completed ✓
2024-05-22 17:01:24,966 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 17:01:25,015 - BERTopic - Representation - Completed ✓
2024-05-22 17:01:25,017 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 17:01:25,023 - BERTopic - Topic reduction - Reduced number of topics from 18 to 18


In [ ]:
topic_model.get_topic(0)

[('profesional', 0.1163644903361299),
 ('educación', 0.11591619953473374),
 ('deportes', 0.11473590547501168),
 ('actividad', 0.11440121879480414),
 ('formación', 0.11303536683882125),
 ('física', 0.11298767716301976),
 ('centros', 0.05137612371353905),
 ('alumnos', 0.03500090399048741),
 ('escolares', 0.033161327320392266),
 ('educativa', 0.0312703244332686)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=14,width=1000,height=1000)

modelo del sexto grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token6'))

2024-05-22 17:01:26,561 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/15 [00:00<?, ?it/s]

2024-05-22 17:01:39,076 - BERTopic - Embedding - Completed ✓
2024-05-22 17:01:39,079 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 17:01:42,459 - BERTopic - Dimensionality - Completed ✓
2024-05-22 17:01:42,463 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 17:01:42,501 - BERTopic - Cluster - Completed ✓
2024-05-22 17:01:42,503 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 17:01:42,539 - BERTopic - Representation - Completed ✓
2024-05-22 17:01:42,540 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 17:01:42,544 - BERTopic - Topic reduction - Reduced number of topics from 14 to 14


In [ ]:
topic_model.get_topic(0)

[('alimentaria', 0.24972189024840885),
 ('pesca', 0.23977298595852),
 ('soberanía', 0.23977298595852),
 ('ganadería', 0.23977298595852),
 ('agricultura', 0.23977298595852),
 ('sector', 0.11479138696393078),
 ('primario', 0.08808983107467586),
 ('actuaciones', 0.053826774506833215),
 ('países', 0.04388484703013118),
 ('condiciones', 0.04388484703013118)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=12,width=1000,height=1000)

modelo del septimo grupo

In [ ]:
topics, probs = topic_model.fit_transform(extractos_token.get('extractos_token7'))

2024-05-22 17:01:43,943 - BERTopic - Embedding - Transforming documents to embeddings.


Batches:   0%|          | 0/14 [00:00<?, ?it/s]

2024-05-22 17:01:55,990 - BERTopic - Embedding - Completed ✓
2024-05-22 17:01:55,993 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
2024-05-22 17:01:59,242 - BERTopic - Dimensionality - Completed ✓
2024-05-22 17:01:59,245 - BERTopic - Cluster - Start clustering the reduced embeddings
2024-05-22 17:01:59,287 - BERTopic - Cluster - Completed ✓
2024-05-22 17:01:59,289 - BERTopic - Representation - Extracting topics from clusters using representation models.
2024-05-22 17:01:59,343 - BERTopic - Representation - Completed ✓
2024-05-22 17:01:59,349 - BERTopic - Topic reduction - Reducing number of topics
2024-05-22 17:01:59,355 - BERTopic - Topic reduction - Reduced number of topics from 15 to 15


In [ ]:
topic_model.get_topic(0)

[('educación', 0.13774954306804013),
 ('profesional', 0.13774954306804013),
 ('deportes', 0.1367255621082251),
 ('actividad', 0.13533288441772365),
 ('física', 0.13495247876861927),
 ('formación', 0.1323725755248993),
 ('hierro', 0.034908113386995704),
 ('ceip', 0.033372770029436775),
 ('centros', 0.027747085253084225),
 ('educativos', 0.025809420810550442)]

In [ ]:
topic_model.visualize_topics()

In [ ]:
topic_model.visualize_distribution(probs[0],min_probability=0.001)

In [ ]:
topic_model.visualize_hierarchy(top_n_topics=50)

In [ ]:
topic_model.visualize_barchart(top_n_topics=77)

In [ ]:
topic_model.visualize_heatmap(n_clusters=11,width=1000,height=1000)